In [1]:
# This is necessary to recognize the modules
import os
import sys
from decimal import Decimal

root_path = os.path.abspath(os.path.join(os.getcwd(), '../..'))
sys.path.append(root_path)

In [15]:
from hummingbot.strategy_v2.backtesting.controllers_backtesting.directional_trading_backtesting import DirectionalTradingBacktesting
from controllers.directional_trading.xtreet_bb import XtreetBBControllerConfig

import datetime


backtesting_engine = DirectionalTradingBacktesting()

config = XtreetBBControllerConfig(
    connector_name="binance_perpetual",
    trading_pair="AI-USDT",
    total_amount_quote=Decimal("1000"),
    candles_connector="binance_perpetual",
    candles_trading_pair="AI-USDT",
    interval="1m",
    bb_length=200,
    bb_std=2,
    dca_spreads=[Decimal("0.0"), Decimal("0.04")],
    dca_amounts_pct=[Decimal("1"), Decimal("4.76")],
    take_profit=Decimal("0.013"),
    stop_loss=Decimal("0.022"),
    time_limit=60 * 60 * 8,
    max_executors_per_side=1,
)

In [16]:

start_time = datetime.datetime(2024, 8, 1).timestamp()
end_time = datetime.datetime(2024, 8, 14).timestamp()

backtesting_results = await backtesting_engine.run_backtesting(
    controller_config=config, trade_cost=0.0006,
    start=int(start_time), end=int(end_time), backtesting_resolution="1m")
df = backtesting_results["processed_data"]["features"]
executors = backtesting_results["executors"]
results = backtesting_results["results"]

2024-08-16 20:41:37,449 - asyncio - ERROR - Unclosed client session
client_session: <aiohttp.client.ClientSession object at 0x1440ed8a0>
2024-08-16 20:41:37,450 - asyncio - ERROR - Unclosed connector
connections: ['[(<aiohttp.client_proto.ResponseHandler object at 0x144726f80>, 181465.191418041)]']
connector: <aiohttp.connector.TCPConnector object at 0x1440ecbe0>


In [17]:
from plotly.subplots import make_subplots
import pandas as pd
import numpy as np
import plotly.graph_objects as go

from hummingbot.connector.connector_base import TradeType



def get_bt_candlestick_trace(df):
    df.index = pd.to_datetime(df.timestamp, unit='s')
    return go.Scatter(x=df.index,
                      y=df['close'],
                      mode='lines',
                      line=dict(color="blue"),
                      )

def get_pnl_trace(executors):
    pnl = [e.net_pnl_quote for e in executors]
    cum_pnl = np.cumsum(pnl)
    return go.Scatter(
        x=pd.to_datetime([e.close_timestamp for e in executors], unit="s"),
        y=cum_pnl,
        mode='lines',
        line=dict(color='gold', width=2, dash="dash"),
        name='Cumulative PNL'
    )

def get_default_layout(title=None, height=800, width=1800):
    layout = {
        "template": "plotly_dark",
        "plot_bgcolor": 'rgba(0, 0, 0, 0)',  # Transparent background
        "paper_bgcolor": 'rgba(0, 0, 0, 0.1)',  # Lighter shade for the paper
        "font": {"color": 'white', "size": 12},  # Consistent font color and size
        "height": height,
        "width": width,
        "margin": {"l": 20, "r": 20, "t": 50, "b": 20},
        "xaxis_rangeslider_visible": False,
        "hovermode": "x unified",
        "showlegend": False,
    }
    if title:
        layout["title"] = title
    return layout

def add_executors_trace(fig, executors, row, col):
    for executor in executors:
        entry_time = pd.to_datetime(executor.timestamp, unit='s')
        entry_price = executor.custom_info["current_position_average_price"]
        exit_time = pd.to_datetime(executor.close_timestamp, unit='s')
        exit_price = executor.custom_info["close_price"]
        name = "Buy Executor" if executor.config.side == TradeType.BUY else "Sell Executor"

        if executor.filled_amount_quote == 0:
            fig.add_trace(go.Scatter(x=[entry_time, exit_time], y=[entry_price, entry_price], mode='lines',
                                     line=dict(color='grey', width=2, dash="dash"), name=name), row=row, col=col)
        else:
            if executor.net_pnl_quote > Decimal(0):
                fig.add_trace(go.Scatter(x=[entry_time, exit_time], y=[entry_price, exit_price], mode='lines',
                                         line=dict(color='green', width=3), name=name), row=row, col=col)
            else:
                fig.add_trace(go.Scatter(x=[entry_time, exit_time], y=[entry_price, exit_price], mode='lines',
                                         line=dict(color='red', width=3), name=name), row=row, col=col)
                
        # print(f"Entry_time: {entry_time} Exit time: {exit_time}, Exit price: {exit_price}")
    return fig


def create_backtesting_figure(df, executors, config):
    # Create subplots
    fig = make_subplots(rows=2, cols=1, shared_xaxes=True,
                        vertical_spacing=0.02, subplot_titles=('Candlestick', 'PNL Quote'),
                        row_heights=[0.7, 0.3])

    # Add candlestick trace
    fig.add_trace(get_bt_candlestick_trace(df), row=1, col=1)

    # Add executors trace
    fig = add_executors_trace(fig, executors, row=1, col=1)

    # Add PNL trace
    fig.add_trace(get_pnl_trace(executors), row=2, col=1)

    # Apply the theme layout
    layout_settings = get_default_layout(f"Trading Pair: {config['trading_pair']}")
    layout_settings["showlegend"] = False
    fig.update_layout(**layout_settings)

    # Update axis properties
    fig.update_xaxes(rangeslider_visible=False, row=1, col=1)
    fig.update_xaxes(row=2, col=1)
    fig.update_yaxes(title_text="Price", row=1, col=1)
    fig.update_yaxes(title_text="PNL", row=2, col=1)
    return fig

fig = create_backtesting_figure(
        df=df,
        executors=executors,
        config=config.dict())
fig.add_trace(go.Scatter(x=df.index,
                                    y=df[f"BBU_{config.bb_length}_{config.bb_std}"])
                        )
fig.add_trace(go.Scatter(x=df.index,
                                    y=df[f"BBM_{config.bb_length}_{config.bb_std}"])
                        )
fig.add_trace(go.Scatter(x=df.index,
                                    y=df[f"BBL_{config.bb_length}_{config.bb_std}"])
                        )
cols_to_show = ["net_pnl_quote", "total_volume", "close_types", "sharpe_ratio", "profit_factor", "max_drawdown_usd"]
print(results)
fig.show()

{'net_pnl': -0.027778011430394104, 'net_pnl_quote': -27.778011430394102, 'total_executors': 62, 'total_executors_with_position': 62, 'total_volume': 51277.77777777778, 'total_long': 35, 'total_short': 27, 'close_types': {'STOP_LOSS': 9, 'TAKE_PROFIT': 47, 'TIME_LIMIT': 6}, 'accuracy_long': 0.7714285714285715, 'accuracy_short': 0.7407407407407407, 'total_positions': 62, 'accuracy': 0.7580645161290323, 'max_drawdown_usd': -100.31688225655215, 'max_drawdown_pct': -0.10006596679987709, 'sharpe_ratio': -0.3171156204072098, 'profit_factor': 0.8762393961667941, 'win_signals': 47, 'loss_signals': 15}
